# Merge Labels
The script merges labels from our prediction and Ariadne. 

In [1]:
import os, sys
import itertools
import numpy as np
from tqdm.notebook import trange

# image
import cv2
import glob 
from skimage.io import imread, imsave, imshow
from PIL import Image, ImageTk
from imutils import paths
import matplotlib.pyplot as plt 
import itertools
import numpy as np
from tqdm.notebook import trange, tqdm_notebook

# image
import cv2
from skimage.io import imread, imsave, imshow
from PIL import Image, ImageTk
from imutils import paths
import matplotlib.pyplot as plt

# customized function
from core.imageprep import dir_checker, random_crop, crop_generator, random_crop_batch
from core.imageprep import create_crop_idx, crop_to_patch, construct_from_patch, create_crop_idx_whole

In [2]:
# on mac
# main_path = "/Volumes/LaCie_DataStorage/PerlmutterData/"

# on Windows
main_path = os.path.join("D:", "PerlmutterData")

img_folder = "segmentation_compiled_export"
folder_raw = "raw_img"

ip_path = os.path.join(main_path, img_folder, 'input')
dir_checker('output', os.path.join(main_path, img_folder))
dir_checker('output_AND', os.path.join(main_path, img_folder))

rawflist = glob.glob(os.path.join(ip_path, folder_raw, '*[!.db]'))
print(rawflist)

# rawflist= [rawflist[-1]]

foldernames = [os.path.basename(x) for x in rawflist]
print(foldernames)

labelname = {
    1: 'cell_membrane',
    2: 'nucleus',
    3: 'nucleolus',
    4: 'lipid_droplet',
    5: 'mito',
    6: 'inclusion',
    7: 'ER',
    8: 'cristae',
}

'''
labelname = {
    1: 'cell_membrane',
    2: 'nucleus',
    3: 'nucleolus',
    4: 'lipid_droplet',
    5: 'mito',
}
'''
print(labelname)

output does not exist in D:PerlmutterData\segmentation_compiled_export
output_AND exists in D:PerlmutterData\segmentation_compiled_export
['D:PerlmutterData\\segmentation_compiled_export\\input\\raw_img\\data_d00_batch01_loc01', 'D:PerlmutterData\\segmentation_compiled_export\\input\\raw_img\\data_d00_batch02_loc02', 'D:PerlmutterData\\segmentation_compiled_export\\input\\raw_img\\data_d00_batch02_loc03', 'D:PerlmutterData\\segmentation_compiled_export\\input\\raw_img\\data_d07_batch01_loc01', 'D:PerlmutterData\\segmentation_compiled_export\\input\\raw_img\\data_d07_batch02_loc01', 'D:PerlmutterData\\segmentation_compiled_export\\input\\raw_img\\data_d07_batch02_loc02', 'D:PerlmutterData\\segmentation_compiled_export\\input\\raw_img\\data_d14_batch01_loc01', 'D:PerlmutterData\\segmentation_compiled_export\\input\\raw_img\\data_d17_batch01_loc01', 'D:PerlmutterData\\segmentation_compiled_export\\input\\raw_img\\data_d21_batch01_loc01']
['data_d00_batch01_loc01', 'data_d00_batch02_loc02'

In [3]:
len(labelname)

8

In [4]:
class sample: 
    def __init__(self, foldername):
        self.foldername = os.path.basename(foldername)
        
    def merge(self, path, labels):
        print(self.foldername)
        print(path)
        
        # set up path
        filelist = {}
        filelist['raw_img'] = glob.glob(os.path.join(path, 'input', 'raw_img', self.foldername, '*.tif'))

        new_labels = {}
        for key, item in labels.items():
            filelist_tmp = glob.glob(os.path.join(path, 'input', item, self.foldername, '*.tif*'))
            if len(filelist_tmp) != 0:
                filelist[item] = filelist_tmp 
                new_labels[key] = item

        img_tmp = imread(filelist['raw_img'][0])
        img_y, img_x = img_tmp.shape

        dir_checker(self.foldername, os.path.join(path, 'output'))
        
        for idx in tqdm_notebook(range(len(filelist['raw_img'])), leave=False):
            img_tmp_base = np.zeros([img_y, img_x, len(labels)], dtype= 'uint8')
            
            for j, label in new_labels.items():
                open_filename = os.path.join(path, 'input', label, self.foldername, filelist[label][idx])
                img_open = imread(open_filename)
                img_open = img_open.astype('uint8')
                img_tmp_base[:, :, j-1] = img_open * (j)
            
            img_tmp_result = np.amax(img_tmp_base, axis=2)
            imsave(os.path.join(path, 'output', self.foldername, str(idx).zfill(4) + '.tif'), img_tmp_result)
            
    def mask_cell(self, path, labels, label_master):
        print(self.foldername)
        print(path)
        
        # set up path
        filelist = {}
        filelist['raw_img'] = glob.glob(os.path.join(path, 'input', 'raw_img', self.foldername, '*.tif'))

        new_labels = {}
        for key, item in labels.items():
            filelist_tmp = glob.glob(os.path.join(path, 'input', item, self.foldername, '*.tif*'))
            if len(filelist_tmp) != 0:
                filelist[item] = filelist_tmp 
                new_labels[key] = item

        img_tmp = imread(filelist['raw_img'][0])
        img_y, img_x = img_tmp.shape
        
        # remove cell_membrane from the list
        master_label = new_labels.pop(1)
        
        # create output folders
        for j, label in new_labels.items():
            dir_checker(label, os.path.join(path, 'output_AND'))
            dir_checker(self.foldername, os.path.join(path, 'output_AND', label))
        
        
        for idx in tqdm_notebook(range(len(filelist['raw_img'])), leave=False):
            img_master_path = os.path.join(filelist[label_master][idx])
            img_master = imread(img_master_path)
            img_master = img_master.astype('uint8')
            img_master = img_master > 0
            
            for j, label in new_labels.items():
                open_filename = os.path.join(filelist[label][idx])
                img_open = imread(open_filename)
                img_open = img_open.astype('uint8')
                img_open = img_open > 0
                output_image = np.logical_and(img_master, img_open)
                output_image = output_image.astype(int)
                imsave(os.path.join(path, 'output_AND', label, self.foldername, str(idx).zfill(4) + '.tif'), output_image)

In [ ]:
for foldername in rawflist: 
    folder_tmp = sample(foldername)
    print(folder_tmp.foldername)
    folder_tmp.mask_cell(os.path.join(main_path, img_folder), labelname, label_master = 'cell_membrane')

data_d00_batch01_loc01
data_d00_batch01_loc01
D:PerlmutterData\segmentation_compiled_export
nucleus exists in D:PerlmutterData\segmentation_compiled_export\output_AND
data_d00_batch01_loc01 exists in D:PerlmutterData\segmentation_compiled_export\output_AND\nucleus
nucleolus exists in D:PerlmutterData\segmentation_compiled_export\output_AND
data_d00_batch01_loc01 exists in D:PerlmutterData\segmentation_compiled_export\output_AND\nucleolus
lipid_droplet exists in D:PerlmutterData\segmentation_compiled_export\output_AND
data_d00_batch01_loc01 exists in D:PerlmutterData\segmentation_compiled_export\output_AND\lipid_droplet
mito exists in D:PerlmutterData\segmentation_compiled_export\output_AND
data_d00_batch01_loc01 exists in D:PerlmutterData\segmentation_compiled_export\output_AND\mito
ER exists in D:PerlmutterData\segmentation_compiled_export\output_AND
data_d00_batch01_loc01 exists in D:PerlmutterData\segmentation_compiled_export\output_AND\ER
cristae exists in D:PerlmutterData\segmenta

C:\Users\wucci_admin\Anaconda3\envs\tfdl02\lib\site-packages\ipykernel_launcher.py:77: UserWarning: D:PerlmutterData\segmentation_compiled_export\output_AND\nucleus\data_d00_batch01_loc01\0000.tif is a low contrast image
C:\Users\wucci_admin\Anaconda3\envs\tfdl02\lib\site-packages\ipykernel_launcher.py:77: UserWarning: D:PerlmutterData\segmentation_compiled_export\output_AND\nucleolus\data_d00_batch01_loc01\0000.tif is a low contrast image
C:\Users\wucci_admin\Anaconda3\envs\tfdl02\lib\site-packages\ipykernel_launcher.py:77: UserWarning: D:PerlmutterData\segmentation_compiled_export\output_AND\lipid_droplet\data_d00_batch01_loc01\0000.tif is a low contrast image
C:\Users\wucci_admin\Anaconda3\envs\tfdl02\lib\site-packages\ipykernel_launcher.py:77: UserWarning: D:PerlmutterData\segmentation_compiled_export\output_AND\mito\data_d00_batch01_loc01\0000.tif is a low contrast image
C:\Users\wucci_admin\Anaconda3\envs\tfdl02\lib\site-packages\ipykernel_launcher.py:77: UserWarning: D:Perlmutte

C:\Users\wucci_admin\Anaconda3\envs\tfdl02\lib\site-packages\ipykernel_launcher.py:77: UserWarning: D:PerlmutterData\segmentation_compiled_export\output_AND\lipid_droplet\data_d00_batch01_loc01\0006.tif is a low contrast image
C:\Users\wucci_admin\Anaconda3\envs\tfdl02\lib\site-packages\ipykernel_launcher.py:77: UserWarning: D:PerlmutterData\segmentation_compiled_export\output_AND\mito\data_d00_batch01_loc01\0006.tif is a low contrast image
C:\Users\wucci_admin\Anaconda3\envs\tfdl02\lib\site-packages\ipykernel_launcher.py:77: UserWarning: D:PerlmutterData\segmentation_compiled_export\output_AND\ER\data_d00_batch01_loc01\0006.tif is a low contrast image
C:\Users\wucci_admin\Anaconda3\envs\tfdl02\lib\site-packages\ipykernel_launcher.py:77: UserWarning: D:PerlmutterData\segmentation_compiled_export\output_AND\cristae\data_d00_batch01_loc01\0006.tif is a low contrast image
C:\Users\wucci_admin\Anaconda3\envs\tfdl02\lib\site-packages\ipykernel_launcher.py:77: UserWarning: D:PerlmutterData\s

C:\Users\wucci_admin\Anaconda3\envs\tfdl02\lib\site-packages\ipykernel_launcher.py:77: UserWarning: D:PerlmutterData\segmentation_compiled_export\output_AND\nucleus\data_d00_batch01_loc01\0013.tif is a low contrast image
C:\Users\wucci_admin\Anaconda3\envs\tfdl02\lib\site-packages\ipykernel_launcher.py:77: UserWarning: D:PerlmutterData\segmentation_compiled_export\output_AND\nucleolus\data_d00_batch01_loc01\0013.tif is a low contrast image
C:\Users\wucci_admin\Anaconda3\envs\tfdl02\lib\site-packages\ipykernel_launcher.py:77: UserWarning: D:PerlmutterData\segmentation_compiled_export\output_AND\lipid_droplet\data_d00_batch01_loc01\0013.tif is a low contrast image
C:\Users\wucci_admin\Anaconda3\envs\tfdl02\lib\site-packages\ipykernel_launcher.py:77: UserWarning: D:PerlmutterData\segmentation_compiled_export\output_AND\mito\data_d00_batch01_loc01\0013.tif is a low contrast image
C:\Users\wucci_admin\Anaconda3\envs\tfdl02\lib\site-packages\ipykernel_launcher.py:77: UserWarning: D:Perlmutte

C:\Users\wucci_admin\Anaconda3\envs\tfdl02\lib\site-packages\ipykernel_launcher.py:77: UserWarning: D:PerlmutterData\segmentation_compiled_export\output_AND\cristae\data_d00_batch01_loc01\0019.tif is a low contrast image
C:\Users\wucci_admin\Anaconda3\envs\tfdl02\lib\site-packages\ipykernel_launcher.py:77: UserWarning: D:PerlmutterData\segmentation_compiled_export\output_AND\nucleus\data_d00_batch01_loc01\0020.tif is a low contrast image
C:\Users\wucci_admin\Anaconda3\envs\tfdl02\lib\site-packages\ipykernel_launcher.py:77: UserWarning: D:PerlmutterData\segmentation_compiled_export\output_AND\nucleolus\data_d00_batch01_loc01\0020.tif is a low contrast image
C:\Users\wucci_admin\Anaconda3\envs\tfdl02\lib\site-packages\ipykernel_launcher.py:77: UserWarning: D:PerlmutterData\segmentation_compiled_export\output_AND\lipid_droplet\data_d00_batch01_loc01\0020.tif is a low contrast image
C:\Users\wucci_admin\Anaconda3\envs\tfdl02\lib\site-packages\ipykernel_launcher.py:77: UserWarning: D:Perlmu

...

C:\Users\wucci_admin\Anaconda3\envs\tfdl02\lib\site-packages\ipykernel_launcher.py:77: UserWarning: D:PerlmutterData\segmentation_compiled_export\output_AND\inclusion\data_d07_batch01_loc01\0521.tif is a low contrast image
C:\Users\wucci_admin\Anaconda3\envs\tfdl02\lib\site-packages\ipykernel_launcher.py:77: UserWarning: D:PerlmutterData\segmentation_compiled_export\output_AND\ER\data_d07_batch01_loc01\0521.tif is a low contrast image
C:\Users\wucci_admin\Anaconda3\envs\tfdl02\lib\site-packages\ipykernel_launcher.py:77: UserWarning: D:PerlmutterData\segmentation_compiled_export\output_AND\cristae\data_d07_batch01_loc01\0521.tif is a low contrast image
C:\Users\wucci_admin\Anaconda3\envs\tfdl02\lib\site-packages\ipykernel_launcher.py:77: UserWarning: D:PerlmutterData\segmentation_compiled_export\output_AND\nucleus\data_d07_batch01_loc01\0522.tif is a low contrast image
C:\Users\wucci_admin\Anaconda3\envs\tfdl02\lib\site-packages\ipykernel_launcher.py:77: UserWarning: D:PerlmutterData\se

C:\Users\wucci_admin\Anaconda3\envs\tfdl02\lib\site-packages\ipykernel_launcher.py:77: UserWarning: D:PerlmutterData\segmentation_compiled_export\output_AND\nucleus\data_d07_batch01_loc01\0527.tif is a low contrast image
C:\Users\wucci_admin\Anaconda3\envs\tfdl02\lib\site-packages\ipykernel_launcher.py:77: UserWarning: D:PerlmutterData\segmentation_compiled_export\output_AND\nucleolus\data_d07_batch01_loc01\0527.tif is a low contrast image
C:\Users\wucci_admin\Anaconda3\envs\tfdl02\lib\site-packages\ipykernel_launcher.py:77: UserWarning: D:PerlmutterData\segmentation_compiled_export\output_AND\lipid_droplet\data_d07_batch01_loc01\0527.tif is a low contrast image
C:\Users\wucci_admin\Anaconda3\envs\tfdl02\lib\site-packages\ipykernel_launcher.py:77: UserWarning: D:PerlmutterData\segmentation_compiled_export\output_AND\mito\data_d07_batch01_loc01\0527.tif is a low contrast image
C:\Users\wucci_admin\Anaconda3\envs\tfdl02\lib\site-packages\ipykernel_launcher.py:77: UserWarning: D:Perlmutte

C:\Users\wucci_admin\Anaconda3\envs\tfdl02\lib\site-packages\ipykernel_launcher.py:77: UserWarning: D:PerlmutterData\segmentation_compiled_export\output_AND\cristae\data_d07_batch01_loc01\0532.tif is a low contrast image
C:\Users\wucci_admin\Anaconda3\envs\tfdl02\lib\site-packages\ipykernel_launcher.py:77: UserWarning: D:PerlmutterData\segmentation_compiled_export\output_AND\nucleus\data_d07_batch01_loc01\0533.tif is a low contrast image
C:\Users\wucci_admin\Anaconda3\envs\tfdl02\lib\site-packages\ipykernel_launcher.py:77: UserWarning: D:PerlmutterData\segmentation_compiled_export\output_AND\nucleolus\data_d07_batch01_loc01\0533.tif is a low contrast image
C:\Users\wucci_admin\Anaconda3\envs\tfdl02\lib\site-packages\ipykernel_launcher.py:77: UserWarning: D:PerlmutterData\segmentation_compiled_export\output_AND\lipid_droplet\data_d07_batch01_loc01\0533.tif is a low contrast image
C:\Users\wucci_admin\Anaconda3\envs\tfdl02\lib\site-packages\ipykernel_launcher.py:77: UserWarning: D:Perlmu

C:\Users\wucci_admin\Anaconda3\envs\tfdl02\lib\site-packages\ipykernel_launcher.py:77: UserWarning: D:PerlmutterData\segmentation_compiled_export\output_AND\inclusion\data_d07_batch01_loc01\0538.tif is a low contrast image
C:\Users\wucci_admin\Anaconda3\envs\tfdl02\lib\site-packages\ipykernel_launcher.py:77: UserWarning: D:PerlmutterData\segmentation_compiled_export\output_AND\ER\data_d07_batch01_loc01\0538.tif is a low contrast image
C:\Users\wucci_admin\Anaconda3\envs\tfdl02\lib\site-packages\ipykernel_launcher.py:77: UserWarning: D:PerlmutterData\segmentation_compiled_export\output_AND\cristae\data_d07_batch01_loc01\0538.tif is a low contrast image
C:\Users\wucci_admin\Anaconda3\envs\tfdl02\lib\site-packages\ipykernel_launcher.py:77: UserWarning: D:PerlmutterData\segmentation_compiled_export\output_AND\nucleus\data_d07_batch01_loc01\0539.tif is a low contrast image
C:\Users\wucci_admin\Anaconda3\envs\tfdl02\lib\site-packages\ipykernel_launcher.py:77: UserWarning: D:PerlmutterData\se

C:\Users\wucci_admin\Anaconda3\envs\tfdl02\lib\site-packages\ipykernel_launcher.py:77: UserWarning: D:PerlmutterData\segmentation_compiled_export\output_AND\nucleus\data_d07_batch01_loc01\0544.tif is a low contrast image
C:\Users\wucci_admin\Anaconda3\envs\tfdl02\lib\site-packages\ipykernel_launcher.py:77: UserWarning: D:PerlmutterData\segmentation_compiled_export\output_AND\nucleolus\data_d07_batch01_loc01\0544.tif is a low contrast image
C:\Users\wucci_admin\Anaconda3\envs\tfdl02\lib\site-packages\ipykernel_launcher.py:77: UserWarning: D:PerlmutterData\segmentation_compiled_export\output_AND\lipid_droplet\data_d07_batch01_loc01\0544.tif is a low contrast image
C:\Users\wucci_admin\Anaconda3\envs\tfdl02\lib\site-packages\ipykernel_launcher.py:77: UserWarning: D:PerlmutterData\segmentation_compiled_export\output_AND\mito\data_d07_batch01_loc01\0544.tif is a low contrast image
C:\Users\wucci_admin\Anaconda3\envs\tfdl02\lib\site-packages\ipykernel_launcher.py:77: UserWarning: D:Perlmutte